# TerraFirma UKESM long-term stabilisation and overshoot scenarios

#### Steps to do
- decide how the bias correction should be applied
    - according to Tom Mitcham: simulation years 10 to 50 of the ramp-up phase are most equal to 1975-2025 in terms of warming trend
          - global mean temperature is similar (+0.26°C), but there is another period (simulation year 0 to 40 which would fit better
    - [ ] double-check the warming trend?
- [ ] create a `process_terrafirma_ukesm_data()`,
- [ ] test with HEF using W5E5 or ERA5, RGI7?, regional spinup ...
        - do they need that we start from pre-industrial state, or would it be ok, if we just start at simulation year 30 (which would correspond best to a "climate" as we had around year 2000, which is around RGI/glavier volume inventory year ... I guess the problem is that their ice sheet / sea-level rise output will be relative to "pre-industrial", and therefore, we also need the glaciers to have the "pre-industrial" baseline...? 
- [ ] do I need to do sth. about the growing out of border issue ...https://github.com/OGGM/oggm/issues/1822 
          

In [65]:
import xarray as xr
xr.set_options(use_new_combine_kwarg_defaults=True)
import numpy as np
import matplotlib.pyplot as plt

- "esm-up2p0" is the "ramp-up" phase.
- "esm-up2p0-gwl2p0" is stabilisation at 2C 
- "esm-up2p0-gwl2p0-50y-dn2p0" is a "ramp-down" from the 2C stabilisation after 50 years'
- "esm-up2p0-gwl4p0" is stabilisation at 4C
- "esm-up2p0-gwl4p0-50y-dn2p0" is a "ramp-down" from the 4C stabilisation after 50 years'
- "esm-hist" is the same model (UKESM1.2-LL) being forced through the CMIP historical forcing'
- "esm-piControl" is the same model with pre-industrial forcing'

In [66]:
variables = ['pr','tas']
period = '205001-213912'
scenarios = ['hist',  # same model (UKESM1.2-LL) being forced through the CMIP historical forcing
             'up2p0', # ramp-up phase
             'up2p0-gwl2p0',  # stabilisation at 2°C
             'up2p0-gwl2p0-50y-dn2p0', # "ramp-down" from 2C stabilisation after 50 years'
             'up2p0-gwl4p0',  # stabilisation at 4C
             "up2p0-gwl4p0-50y-dn2p0",  # "ramp-down" from 4C stabilisation after 50 years'
             "piControl"  # same model with pre-industrial forcing'
            ]

In [67]:
time_coder = xr.coders.CFDatetimeCoder(use_cftime=True)
run = False
if run:
    for var in ['pr','tas']:
        _dt = xr.open_mfdataset(f'terrafirma_data/raw_data/{var}_Amon_UKESM1-2-LL_esm-{scen}_r1i1p1f1_gn_*.nc', 
                                decode_times=time_coder).load()
        if var == 'tas':
            _dt['tas']  = _dt.tas
            _dt.tas.attrs['units'] = '°C'
        else:
            # already in correct format... 
            assert 'kg m-2 s-1' in _dt.pr.units, 'Precip units not understood'
        _dt = _dt.drop_vars(['time_bnds','lat_bnds', 'lon_bnds'])
        y0=_dt.time.dt.year.values[0]
        y1=_dt.time.dt.year.values[-1]
        _dt.to_netcdf(f'terrafirma_data/{var}_Amon_UKESM1-2-LL_esm-{scen}_r1i1p1f1_gn.nc')

In [91]:
run = False
if run:
    for var in ['pr','tas']:
        time_coder = xr.coders.CFDatetimeCoder(use_cftime=True)
        global_var_mean_dict = {}
        for scen in scenarios:
            _dt = xr.open_dataset(f'terrafirma_data/{var}_Amon_UKESM1-2-LL_esm-{scen}_r1i1p1f1_gn.nc',
                                 decode_times=time_coder).groupby('time.year').mean().load()
            ### check the global mean temperature and precipitation time series
            # weighted average over latitudes
            if var == 'tas':
                _dt[var] = _dt[var]-273.15
            weight = np.cos(np.deg2rad(_dt.lat))
            weight = weight / weight.sum()
            global_var_mean_dict[scen] = (_dt.mean(dim='lon') * weight).sum(dim='lat')
        keys = list(global_var_mean_dict.keys())
        vals = list(global_var_mean_dict.values())

        ds_global_var_mean = xr.concat(vals, dim="scenario", join='outer')
        ds_global_var_mean = ds_global_var_mean.assign_coords(scenario=keys)
        ds_global_var_mean.to_netcdf(f'terrafirma_global_annual_mean_{var}_scenarios.nc')
ds_global_tas_mean = xr.open_dataset('terrafirma_global_annual_mean_tas_scenarios.nc')
ds_global_pr_mean = xr.open_dataset('terrafirma_global_annual_mean_pr_scenarios.nc')

ds_w5e5 = xr.open_dataset('/home/www/oggm/climate/gswp3-w5e5/unflattened/monthly/gswp3-w5e5_obsclim_tas_global_monthly_1901_2019.nc')
ds_w5e5 = ds_w5e5.groupby('time.year').mean().load()
ds_w5e5['tas'] = ds_w5e5['tas'] -273.15
weight = np.cos(np.deg2rad(ds_w5e5.lat))
weight = weight / weight.sum()
ds_global_tas_mean_w5e5 = (ds_w5e5.mean(dim='lon') * weight).sum(dim='lat')

In [93]:
ds_global_tas_mean

<xarray.Dataset> Size: 45kB
Dimensions:   (scenario: 7, year: 695)
Coordinates:
  * scenario  (scenario) <U22 616B 'hist' 'up2p0' ... 'piControl'
  * year      (year) int64 6kB 1850 1851 1852 1853 1854 ... 2541 2542 2543 2544
    height    float64 8B ...
Data variables:
    tas       (scenario, year) float64 39kB ...

In [92]:
ds_global_tas_mean_w5e5

<xarray.Dataset> Size: 17kB
Dimensions:  (time: 1428)
Coordinates:
  * time     (time) datetime64[ns] 11kB 1901-01-01 1901-02-01 ... 2019-12-01
Data variables:
    tas      (time) float32 6kB 11.64 12.03 12.67 13.7 ... 14.89 13.75 13.23

In [87]:
# standard deviation up2p0 ramp-up 
std_ref_period_up2p0 = ds_global_tas_mean.sel(scenario='up2p0').sel(year=slice(1850,1889)).std().tas.values
# standard deviation historical  
std_ref_period_hist = ds_global_tas_mean.sel(scenario='hist').sel(year=slice(1975,2014)).std().tas.values
print(std_ref_period_hist, std_ref_period_up2p0, 'std up2p0 vs historical', std_ref_period_up2p0/std_ref_period_hist)

0.37814055952857206 0.3314687672223995 0.8765755454417312


<xarray.Dataset> Size: 1GB
Dimensions:  (time: 1428, lat: 360, lon: 720)
Coordinates:
  * time     (time) datetime64[ns] 11kB 1901-01-01 1901-02-01 ... 2019-12-01
  * lat      (lat) float32 1kB 89.75 89.25 88.75 88.25 ... -88.75 -89.25 -89.75
  * lon      (lon) float32 3kB -179.8 -179.2 -178.8 -178.2 ... 178.8 179.2 179.8
Data variables:
    tas      (time, lat, lon) float32 1GB ...
Attributes:
    title:                     GSWP3-W5E5 observational climate input data fo...
    institution:               Potsdam Institute for Climate Impact Research ...
    project:                   Inter-Sectoral Impact Model Intercomparison Pr...
    contact:                   ISIMIP cross-sectoral science team <info@isimi...
    summary:                   GSWP3 v1.09 bias-adjusted to W5E5 v2.0 with IS...
    references:                Kim (2017) <https://doi.org/10.20783/DIAS.501>...
    postprocessing_date:       2022-05-12
    postprocessing_scientist:  lilian.schuster@student.uibk.ac.at
    postprocessing_actions:    using xarray: ds = xr.open_mfdataset(gswp3-w5e...

In [69]:
tas_ann_hist_ref = ds_global_tas_mean.sel(scenario='hist').sel(year=slice(1975,2014)).tas
from scipy.stats import linregress
from scipy.stats import theilslopes

tas_ann = tas_ann_hist_ref
t = tas_ann.year
y = tas_ann.values
res = linregress(t, y)        
ts = theilslopes(y, t)
ref_period_1975_2014_linear_fit_slope = res.slope
ref_period_1975_2014_theil_sen_slope = ts[0]
print("linear fit slope °C/year:", res.slope, ", Theil–Sen slope °C/year:", ts[0])
#print("95% CI lower:", ts[2])
#print("95% CI upper:", ts[3])
ref_period_1975_2014 = ds_global_tas_mean.sel(scenario='hist').tas.sel(year=slice(1975,2014)).mean()

linear fit slope °C/year: 0.028984237786977774 , Theil–Sen slope °C/year: 0.030282438500246388


In [70]:
ds_global_tas_mean.sel(scenario='up2p0').tas.dropna(dim='year')

<xarray.DataArray 'tas' (year: 290)> Size: 2kB
array([13.661966, 13.743564, 13.805403, ..., 19.755408, 19.778811, 19.862972])
Coordinates:
  * year      (year) int64 2kB 1850 1851 1852 1853 1854 ... 2136 2137 2138 2139
    height    float64 8B ...
    scenario  <U22 88B 'up2p0'

In [71]:
import pandas as pd
pd_linear_fit = pd.DataFrame()
for j in np.arange(0,250):
    tas_ann = ds_global_tas_mean.sel(scenario='up2p0').tas.sel(year=slice(1850+j,1889+j))
    t = tas_ann.year
    y = tas_ann.values
    res = linregress(t, y)        
    ts = theilslopes(y, t)
    pd_linear_fit.loc[j+1850,'linear fit slope'] = res.slope
    pd_linear_fit.loc[j+1850, 'Theil-Sen slope'] = ts[0]
    pd_linear_fit.loc[j+1850, 'global_mean_temp'] = tas_ann.mean().values


In [72]:
rolling_40yr_ramp = ds_global_tas_mean.sel(scenario='up2p0').tas.rolling(year=40, center=False).mean().dropna(dim='year') - ref_period_1975_2014
year_match = np.abs(rolling_40yr_ramp).idxmin()
year_match-1850
# when just checking the global average temperature using 1850 to 1889 works best,

<xarray.DataArray 'year' ()> Size: 8B
array(39.)
Coordinates:
    height   float64 8B 1.5

- In my opinion, year 0 to 40 of the ramp up scenario (up2p0) fits best to the historical 1975-2014 period in terms of both, the warming trend and the global mean temperature. However, according to the paper it is year 10 to 50. 

----
- Tom Mitcham: the years 10-50 of the "ramp-up" is nearest to the years 1975-2015 of the "esm-hist" simulation, at least when comparing global average warming across a set time-period compared to the pre-industrial simulation.
- referred paper: "We therefore compare the evolution of the UKESM1.2 CMIP6 historical runs and the TIPMIP ramp-up runs over a common GMSAT space, namely for the 40-year period of observed warming from 0.2°C to 1.0°C and the same 40-year warming period in the ramp-up run. This equates to 1975 to 2015 in the historical runs and years 10 to 50 of the TIPMIP ramp-up."
---

<xarray.DataArray 'year' ()> Size: 8B
array(1889.)
Coordinates:
    height   float64 8B 1.5

In [21]:
for scen in scenarios: 
    plt.plot(ds_global_tas_mean.sel(scenario=scen).year, 
             ds_global_tas_mean.sel(scenario=scen)-ref_period_1975_2014,
             label=scen)
plt.plot(np.arange(1850,1890,1),
         ds_global_tas_mean.sel(scenario='hist').sel(year=slice(1975,2014))-ref_period_1975_2014, color='grey')
plt.axhline(0, lw=2, color='grey')
plt.legend(title = 'Scenarios', bbox_to_anchor=(1, 1.02))
plt.ylabel('Global warming (rel. to 1975-2014)')
plt.savefig('terrafirma_global_warming_scenarios.png')

NameError: name 'ds_global_tas_mean' is not defined

In [ ]:
for scen in scenarios: 
    plt.plot(ds_global_pr_mean.sel(scenario=scen).year, 
             ds_global_pr_mean.sel(scenario=scen)-ref_period_1975_2014,
             label=scen)
plt.plot(np.arange(1850,1890,1),
         ds_global_pr_mean.sel(scenario='hist').sel(year=slice(1975,2014))-ref_period_1975_2014,
         color='grey')
plt.axhline(0, lw=2, color='grey')
plt.legend(title = 'Scenarios', bbox_to_anchor=(1, 1.02))
plt.ylabel('Global average precipitation (kg m-2 year-1)')
plt.savefig('terrafirma_global_mean_precipiation_scenarios.png')

In [73]:
for scen in scenarios: 
    plt.plot(global_pr_mean_dict[scen].year, 
             global_pr_mean_dict[scen], # unit is kg m-2 s-1 --> *60 * 60*24*365.25  (kg m-2 year-1)
             label=scen)
plt.plot(np.arange(1850,1890,1),
         global_tas_mean_dict['hist'].sel(year=slice(1975,2014))-ref_period_1975_2014, color='grey')
plt.axhline(0, lw=2, color='grey')
plt.legend(title = 'Scenarios', bbox_to_anchor=(1, 1.02))
plt.ylabel('Global average precipitation (kg m-2 year-1)')
plt.savefig('terrafirma_global_mean_precipiation_scenarios.png')

NameError: name 'global_pr_mean_dict' is not defined